# 协变量筛选

(scm)=

## mas.model.scm

```{py:class} mas.model.scm

```


(scm-spec)=

### spec()

```{py:method} spec(direction="both", p_forward=0.05, p_backward=0.01, global_init=0.001, maxiter=None, accept_rule=None) -> MarkedScmSpecDefFunctionType

```

标记一个函数作为 scm 配置函数

**参数：**

- **direction** _(`"forward"` | `"backward"` | `"both"`, optional)_: 搜索方向。默认值为`"both"`。
- **p_forward** _(`float`, optional)_: 前向搜索过程中假设检验的显著性水平。即若 p 值小于此值，则纳入此协变量关系。默认值为 `0.05`。
- **p_backward** _(`float`, optional)_: 逆向搜索过程中假设检验的显著性水平。即若 p 值大于此值，则剔除此协变量关系。默认值为 `0.01`。
- **global_init** _(`float`, optional)_: 所有因纳入协变量关系而新增的固定效应参数（theta）初值。默认值为 `1e-3`。
- **maxiter** _(`int`, optional)_: 最大搜索次数。默认值为 `None`。
- **accept_rule** _(`AcceptRuleCallable`, optional)_: 用户自定义的接受规则。

  例如设置自定义接受规则为：仅当纳入协变量后清除率的个体间变异参数方差估计值 `omega["eta_cl", "eta_cl"]` 减小 30% 或以上时才接受新的协变量模型。

  ```python
  def custom_rule(context: AcceptRuleContext) -> bool:
      if context.direction == "forward":
          if context.test_params.omega["eta_cl", "eta_cl"] / context.base_params.omega["eta_cl", "eta_cl"] < 0.7:
              return True
      return False
  ```

**示例：**

```python
@scm.spec(direction="forward", maxiter=20)
def my_scm_spec(m: Warfarin):
    ...
```


(scm-test)=

### test()

```{py:method} test(covariates, on, states, init=None, bounds=None, init_state= None) -> None

```

指定需要被测试的协变量-参数关系。

**参数：**

- **covariates** _(`AnyCategoricalColVar | list[AnyCategoricalColVar] | StrCategoricalColVarCollection | NumericCategoricalColVarCollection | AnyContinuousColVar | list[AnyContinuousColVar] | NumericContinuousColVarCollection | str | list[str]`)_：需要被测试的协变量。一般接受自 {ref}`column() <column>` 或 {ref}`multicolumn() <multicolumn>` 定义的变量。
- **on** _(`Theta | list[Theta] | str | list[str]`)_：需要被引入协变量的固定效应参数。
- **states** _(`AnyCategoricalValidStates | AnyContinuousValidStates`)_：需要被测试的协变量-参数关系状态。对应的协变量效应参数化形式请参考 {ref}`协变量效应参数化公式 <scm-states>`。
  - 对于分类型协变量，支持的状态为 `"exclude"`、`"linear"` 与 `"*"`。
  - 对于连续型协变量，支持的状态为 `"exclude"`、`"linear"`、`"piecewise"`、`"exp"`、`"power"` 与 `"*"`。
- **init** _(`ValueType | list[ValueType | PiecewiseValueType | None]`, optional)_：因纳入协变量关系而新增的协变量效应参数初值。若为 `None`，将自动计算初值。默认值为 `None`。
- **bounds** _(`BoundsType | list[BoundsType | PiecewiseBoundsType | None]`, optional)_：协变量效应参数估计的上下边界值。若为 `None`，将自动计算边界值。默认值为 `None`。
- **init_state** _(`CategoricalValidStateType`, optional)_：在搜索开始时即被引入至模型的协变量关系及其状态。默认值为 `None`。


(scm-states)=

### 协变量效应参数化公式

**总则**

以乘法的形式结合各协变量效应与原模型固定效应参数，公式如下：

$$
p_{ki} = \theta_{k} \times g_{k}({z}_i) + \eta_{ki}
$$

$$
g({z}_i) = \prod_{r = 1}^{q} c_{ir}
$$

假设原模型中共有 k 个固定效应参数与 i 个个体。其中，$p_{ki}$ 为第 i 个个体的第 k 个固定效应参数的估计值；$\theta_{k}$ 为此固定效应参数的群体典型值；$\eta_{ki}$ 为此固定效应参数的个体间变异；${z}_i$ 为第 i 个个体的协变量值向量；$g_{k}$ 为有关于 ${z}_i$ 的函数，用于描述协变量与固定效应参数间的关系，具体由纳入协变量的个数 r 以及不同的协变量-参数关系状态（$c_{ir}$）决定。

**各状态的参数化公式**

- `"exclude"`：不引入任何协变量。
- `"linear"`：以线性关系引入协变量，公式如下：

若为连续型协变量：

$$
c_{ir} = 1 + \theta_{r} \times (z_{ir} - median(z_r))
$$

若为分类协变量（以二分类变量为例）：

$$
c_{ir} = \begin{cases}
    1 & 若 \quad z_{ir} = a \\
    1 + \theta_{r} & 若 \quad z_{ir} = b
\end{cases}
$$

- `"piecewise"`：以分段线性关系引入协变量，公式如下：

$$
c_{ir} = \begin{cases}
    1 + \theta_{r} \times (z_{ir} - median(z_r)) & 若 \quad z_{ir} ≤ median(z_r) \\
    1 + \theta_{r+1} \times (z_{ir} - median(z_r)) & 若 \quad z_{ir} > median(z_r)
\end{cases}
$$

- `"exp"`：以指数形式引入协变量，公式如下：

$$
c_{ir} = exp(\theta_{r} \times (z_{ir} - median(z_r)))
$$

- `"power"`：以幂的形式引入协变量，公式如下：

$$
c_{ir} = \theta_{r}^{z_{ir} - median(z_r)}
$$

上述公式中，$\theta_{r}$ 为协变量效应参数，表明了协变量值的变动对固定效应参数的影响大小。

:::{admonition} 参考文献
:class: tip

_Jonsson, E. N., & Karlsson, M. O. (1998). Automated covariate model building within NONMEM. Pharmaceutical research, 15(9), 1463–1468._
:::

**示例：**

例如，假设在模型固定效应参数清除率（`self.theta_cl`）上以线性关系引入了协变量体重（`self.wt`）与年龄（`self.age`），模型将变为如下形式：

```python
class WarfarinPk(EvOneCmtLinear):
    """
    theta_cl ~ WT @ linear
    theta_cl ~ AGE @ linear
    """

    def __init__(self):
        super().__init__()
        self.theta_cl = theta(0.15, bounds=(0.01, 10.0), fixed=False)
        self.theta_v = theta(8.0, bounds=(0.01, 20.0), fixed=False)
        self.theta_ka = theta(0.5, bounds=(0.01, 5.0), fixed=False)
        self.theta_alag = theta(0.8, bounds=(0.01, 24.0), fixed=False)
        self.WT__theta_cl_1 = theta(-0.003125, bounds=(-0.03125, 0.03333), fixed=False)
        self.AGE__theta_cl_1 = theta(-0.002985, bounds=(-0.02985, 0.1176), fixed=False)
        self.eta_cl = omega(0.05, fixed=False)
        self.eta_v = omega(0.08, fixed=False)
        self.eta_ka = omega(0.05, fixed=False)
        self.eta_alag = omega(0.15, fixed=False)
        self.eps_prop = sigma(0.01, fixed=False)
        self.eps_add = sigma(0.55, fixed=False)
        self.WT = column('WT', dtype='numeric', is_categorical=False)
        self.AGE = column('AGE', dtype='numeric', is_categorical=False)

    def pred(self):
        AGE__theta_cl = 1 + self.AGE__theta_cl_1 * (self.AGE - 29.5)
        theta_cl__with_cov = self.theta_cl * AGE__theta_cl
        WT__theta_cl = 1 + self.WT__theta_cl_1 * (self.WT - 70.0)
        theta_cl__with_cov = theta_cl__with_cov * WT__theta_cl
        cl = theta_cl__with_cov * exp(self.eta_cl)
        v = self.theta_v * exp(self.eta_v)
        ka = self.theta_ka * exp(self.eta_ka)
        alag = self.theta_alag * exp(self.eta_alag)
        pred_res = self.pred_physio(cl=cl, v=v, ka=ka, alag1=alag, s2=v)
        ipred = pred_res.F
        y = ipred * (1 + self.eps_prop) + self.eps_add
        return y
```


(scm-spec-example)=


In [2]:
from mas.model import *
from mas.datasets import warfarin_pk


class WarfarinPk(EvOneCmtLinear):
    def __init__(self) -> None:
        self.theta_cl = theta(0.15, bounds=(0.01, 10))
        self.theta_v = theta(8, bounds=(0.01, 20))
        self.theta_ka = theta(0.5, bounds=(0.01, 5))
        self.theta_alag = theta(0.8, bounds=(0.01, 24))

        self.eta_cl = omega(0.05)
        self.eta_v = omega(0.08)
        self.eta_ka = omega(0.05)
        self.eta_alag = omega(0.15)

        self.eps_prop = sigma(0.01)
        self.eps_add = sigma(0.55)

    def pred(self):
        cl = self.theta_cl * exp(self.eta_cl)  # 指数型个体间变异
        v = self.theta_v * exp(self.eta_v)
        ka = self.theta_ka * exp(self.eta_ka)
        alag = self.theta_alag * exp(self.eta_alag)

        pred_res = self.pred_physio(cl=cl, v=v, ka=ka, alag1=alag, s2=v)  # 使用生理药动学参数预测
        ipred = pred_res.F  # 取出血药浓度预测值

        y = ipred * (1 + self.eps_prop) + self.eps_add  # 比例型与加和型个体内变异

        return y


model = PopModel(WarfarinPk, warfarin_pk)
fit_res = model.fit()

🔧 CXX compiler C:\ProgramData\mingw64\bin\g++.EXE
📦 Compiling build target...
🔗 Linking dynamic library...
✅ Compilation Finished
✈️ First Order Conditional Estimation
Using BFGS...
* maxiter = 9999
* xtol = 1e-06
* ftol = 1e-06
* lower_bounds = 
* upper_bounds = 
* log_level = 0
* print = 1
* print_type = 0
* verbose = 1
* p_small = 0.1
* rel_step_size = 0.001

#0    ofv: 364.3540523
x: 1.0000e-01  1.0000e-01  1.0000e-01  1.0000e-01  1.0000e-01  1.0000e-01  1.0000e-01  1.0000e-01  1.0000e-01  1.0000e-01  

Gradients: 101.0869092 7.448347598 -104.527048 30.99690495 -37.06225844 16.55080045 -45.97759626 -13.85882588 32.8152305 114.4144297 

Funcalls: 8
#1    ofv: 299.5539461
x: -1.6505e-01 8.0470e-02  3.7407e-01  1.8725e-02  1.9718e-01  5.6603e-02  2.2056e-01  1.3634e-01  1.3957e-02  -2.0000e-01 

Gradients: -114.075615 -2.647636428 -72.14488225 10.92768269 -34.00781518 15.79326196 -36.54203627 -12.03106061 38.90196043 85.34205841 

Funcalls: 17
#2    ofv: 265.0144085
x: 8.0508e-02  8.6

In [4]:
@scm.spec
def warfarin_scm_rules(m: WarfarinPk):
    scm.test("WT", on=m.theta_cl, states="*")
    scm.test("WT", on=m.theta_v, states="*")


scm_res = fit_res.scm(warfarin_scm_rules)
scm_res

Starting forward search...
Iteration#1, Testing Branch 1 / 2...
theta_cl ~ WT @ linear
theta_v ~ WT @ exclude
Fitting...
➡️ Since build cache already exists, skip compile
Done
Estimation Summary                                                              

────────────────────────────────────────────────────────────────────────────────
 Estimation   Covariance      OFV         Cond.    
                                          Number   
────────────────────────────────────────────────────────────────────────────────
 ✅ Converged                   213.308             
────────────────────────────────────────────────────────────────────────────────
Number of Ob 250                                   
servations:                                        
Number of    11                                    
Parameters:                                        


Parameter Estimation                                                            

───────────────────────────────────────────────────

Summary                                                                         

────────────────────────────────────────────────────────────────────────────────
    Step         Test         OFV          DDF        P Value      Accepted     Selected      Model    
────────────────────────────────────────────────────────────────────────────────
           1   theta_cl ~ 213.308(+4.6            1 0.030 < 0.05          Yes              WarfarinPk__
              WT @ linear          90)                 (forward)                                    1_1
             theta_v ~ WT 191.380(+26.            1 0.000 < 0.05          Yes            ✅ WarfarinPk__
                 @ linear         618)                 (forward)                                    1_2
           2   theta_cl ~ 186.560(+4.8            1 0.028 < 0.05          Yes            ✅ WarfarinPk__
              WT @ linear          20)                 (forward)                                    2_1
             theta_v ~ WT 191.011(+0.3            1 0.543 > 0.05           No              WarfarinPk__
              @ piecewise          69)                 (forward)                                    2_2
           3   theta_cl ~ 186.033(+0.5            1 0.468 > 0.05           No              WarfarinPk__
                     WT @          27)                 (forward)                                    3_1
                piecewise                                                                              
             theta_v ~ WT 186.202(+0.3            1 0.550 > 0.05           No              WarfarinPk__
              @ piecewise          58)                 (forward)                                    3_2
           4   theta_cl ~    191.380(-           -1 0.028 > 0.01          Yes            ✅ WarfarinPk__
             WT @ exclude       4.820)                (backward)                                    4_1
             theta_v ~ WT    213.308(-           -1 0.000 < 0.01           No              WarfarinPk__
                @ exclude      26.748)                (backward)                                    4_2
           5 theta_v ~ WT    217.997(-           -1 0.000 < 0.01           No              WarfarinPk__
                @ exclude      26.618)                (backward)                                    5_2
────────────────────────────────────────────────────────────────────────────────

## ScmResult

```{py:class} ScmResult()

```

SCM 搜索结果，包含最终模型、运行日志以及各个步骤中的模型结果。

### final_model

```{py:property} final_model

```

SCM 法搜索得到的最终模型。

**类型：**

`ScmFinalModel`


In [5]:
scm_res.final_model

```python
class WarfarinPk__4_1(EvOneCmtLinear):
    """
    theta_v ~ WT @ linear
    """

    def __init__(self):
        super().__init__()
        self.theta_cl = theta(0.13225628140336454, bounds=(0.01, 10.0), fixed=False)
        self.theta_v = theta(8.076371754991348, bounds=(0.01, 20.0), fixed=False)
        self.theta_ka = theta(1.3368408859910255, bounds=(0.01, 5.0), fixed=False)
        self.theta_alag = theta(0.8227523051009413, bounds=(0.01, 24.0), fixed=False)
        self.WT__theta_v_1 = theta(0.013039911125114306, bounds=(-0.03125, 0.03333333333333333), fixed=False)
        self.eta_cl = omega(0.08289638409433286, fixed=False)
        self.eta_v = omega(0.01766768192187216, fixed=False)
        self.eta_ka = omega(0.7037029773125222, fixed=False)
        self.eta_alag = omega(0.15549785963005286, fixed=False)
        self.eps_prop = sigma(0.007529493956931285, fixed=False)
        self.eps_add = sigma(0.06592263102065547, fixed=False)
        self.WT = column('WT', dtype='numeric', is_categorical=False)

    def pred(self):
        WT__theta_cl = 1
        WT__theta_v = 1 + self.WT__theta_v_1 * (self.WT - 70.0)
        theta_cl__with_cov = self.theta_cl * WT__theta_cl
        theta_v__with_cov = self.theta_v * WT__theta_v
        cl = theta_cl__with_cov * exp(self.eta_cl)
        v = theta_v__with_cov * exp(self.eta_v)
        ka = self.theta_ka * exp(self.eta_ka)
        alag = self.theta_alag * exp(self.eta_alag)
        pred_res = self.pred_physio(cl=cl, v=v, ka=ka, alag1=alag, s2=v)
        ipred = pred_res.F
        y = ipred * (1 + self.eps_prop) + self.eps_add
        return y
```


### steps

```{py:property} steps

```

各搜索步骤的模型测试结果。

**类型：**

`list[ScmStepwiseResult]`


(ScmResult-as-dataframe)=

### as_dataframe()

```{py:method} as_dataframe

```

将搜索步骤与结果转为 dataframe 类型

**类型：**

`DataFrame`


In [9]:
scm_res.as_dataframe()

shape: (9, 14)
┌──────┬───────────┬───────────┬───────────┬───┬───────────┬──────────┬──────────┬─────────────────┐
│ step ┆ parameter ┆ covariate ┆ state     ┆ … ┆ direction ┆ accepted ┆ selected ┆ model           │
│ ---  ┆ ---       ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ---      ┆ ---      ┆ ---             │
│ i64  ┆ str       ┆ str       ┆ str       ┆   ┆ str       ┆ bool     ┆ bool     ┆ str             │
╞══════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪══════════╪══════════╪═════════════════╡
│ 0    ┆ theta_cl  ┆ WT        ┆ linear    ┆ … ┆ forward   ┆ true     ┆ false    ┆ WarfarinPk__1_1 │
│ 0    ┆ theta_v   ┆ WT        ┆ linear    ┆ … ┆ forward   ┆ true     ┆ true     ┆ WarfarinPk__1_2 │
│ 1    ┆ theta_cl  ┆ WT        ┆ linear    ┆ … ┆ forward   ┆ true     ┆ true     ┆ WarfarinPk__2_1 │
│ 1    ┆ theta_v   ┆ WT        ┆ piecewise ┆ … ┆ forward   ┆ false    ┆ false    ┆ WarfarinPk__2_2 │
│ 2    ┆ theta_cl  ┆ WT        ┆ piecewise ┆ … ┆ forward   ┆ false    ┆ false    ┆ WarfarinPk__3_1 │
│ 2    ┆ theta_v   ┆ WT        ┆ piecewise ┆ … ┆ forward   ┆ false    ┆ false    ┆ WarfarinPk__3_2 │
│ 3    ┆ theta_cl  ┆ WT        ┆ exclude   ┆ … ┆ backward  ┆ true     ┆ true     ┆ WarfarinPk__4_1 │
│ 3    ┆ theta_v   ┆ WT        ┆ exclude   ┆ … ┆ backward  ┆ false    ┆ false    ┆ WarfarinPk__4_2 │
│ 4    ┆ theta_v   ┆ WT        ┆ exclude   ┆ … ┆ backward  ┆ false    ┆ false    ┆ WarfarinPk__5_2 │
└──────┴───────────┴───────────┴───────────┴───┴───────────┴──────────┴──────────┴─────────────────┘